In [1]:
import pandas as pd
import nltk
import re
import random
from textblob import TextBlob 
import seaborn as sns
import math
import plotly
import plotly.graph_objs as go
from plotly.offline import iplot, init_notebook_mode
import cufflinks
cufflinks.go_offline(connected=True)
init_notebook_mode(connected=True)
import plotly.express as px
import numpy as np
import matplotlib.pyplot as plt 
import chart_studio
import chart_studio.tools as tls
import plotly.figure_factory as ff
import chart_studio.plotly as py
import plotly.io as pio
import os
from statistics import mean
from statistics import median

In [2]:
topics_data = pd.read_csv (r'~/Downloads/topics_safety.csv')
topics_subset=topics_data
figs=[]
#topics_subset=topics_subset.dropna()

In [3]:
topics_subset['comments']=topics_subset['comments'].astype(str)
topics_subset['title']=topics_subset['title'].astype(str)
topics_subset['body']=topics_subset['body'].astype(str)

REPLACE_NO_SPACE = re.compile("[.;:!\'?,\"()\[\]]")
REPLACE_WITH_SPACE = re.compile("(<br\s*/><br\s*/>)|(\-)|(\/)")


#phrases=df_all['Phrase'].tolist()
topics_subset['comments_clean']=topics_subset['comments']
topics_subset['title_clean']=topics_subset['comments']
topics_subset['body_clean']=topics_subset['comments']
# random.shuffle(phrases)
# train_split=.75
# train_len=int(len(phrases)*train_split)
# print(train_len)

# phrases_train = phrases[:train_len]
# phrases_test = phrases[train_len:]

def preprocess_phrase(phrases):
    phrases = [REPLACE_NO_SPACE.sub("", line.lower()) for line in phrases]
    phrases = [REPLACE_WITH_SPACE.sub(" ", line) for line in phrases]
    
    return phrases

topics_subset['comments_clean'] = preprocess_phrase(topics_subset['comments'])
topics_subset['title_clean'] = preprocess_phrase(topics_subset['title'])
topics_subset['body_clean'] = preprocess_phrase(topics_subset['body'])
topics_subset=topics_subset.reset_index(drop=True)

topics_subset['blob']=topics_subset['comments']
topics_subset['sentiment']=topics_subset['comments_clean']
topics_subset['title_sentiment']=topics_subset['comments_clean']
topics_subset['body_sentiment']=topics_subset['comments_clean']
i=0
for i in range(len(topics_subset['comments_clean'])):
    if i%5000==0:
        print(i)
    topics_subset['blob'][i]=TextBlob(topics_subset['comments_clean'][i])
    topics_subset['sentiment'][i]=topics_subset['blob'][i].sentiment.polarity
    topics_subset['title_sentiment'][i]=TextBlob(topics_subset['title_clean'][i]).sentiment.polarity
    topics_subset['body_sentiment'][i]=TextBlob(topics_subset['body_clean'][i]).sentiment.polarity
    
    i=+1

topics_subset['sentiment_skewed']=topics_subset['sentiment']
i=0
for i in range(len(topics_subset['sentiment'])):
    if topics_subset['sentiment'][i]>0:
        topics_subset['sentiment_skewed'][i]=topics_subset['sentiment'][i]*(1+((1-topics_subset['sentiment'][i])**2))
    elif topics_subset['sentiment'][i]<0:
        topics_subset['sentiment_skewed'][i]=topics_subset['sentiment'][i]*(1+((-1-topics_subset['sentiment'][i])**2))
    else:
        topics_subset['sentiment_skewed'][i]=0
    i=+1
print('got this far')
    
topics_subset['title_skewed']=topics_subset['sentiment']
i=0
for i in range(len(topics_subset['sentiment'])):
    if topics_subset['title_sentiment'][i]>0:
        topics_subset['title_skewed'][i]=topics_subset['title_sentiment'][i]*(1+((1-topics_subset['title_sentiment'][i])**2))
    elif topics_subset['title_sentiment'][i]<0:
        topics_subset['title_skewed'][i]=topics_subset['title_sentiment'][i]*(1+((-1-topics_subset['title_sentiment'][i])**2))
    else:
        topics_subset['title_skewed'][i]=0
    i=+1
print('even further now')
    
topics_subset['body_skewed']=topics_subset['sentiment']
i=0
for i in range(len(topics_subset['sentiment'])):
    if topics_subset['body_sentiment'][i]>0:
        topics_subset['body_skewed'][i]=topics_subset['body_sentiment'][i]*(1+((1-topics_subset['body_sentiment'][i])**2))
    elif topics_subset['body_sentiment'][i]<0:
        topics_subset['body_skewed'][i]=topics_subset['body_sentiment'][i]*(1+((-1-topics_subset['body_sentiment'][i])**2))
    else:
        topics_subset['body_skewed'][i]=0
    i=+1

topics_subset['sentiment']=topics_subset['sentiment'].apply(pd.to_numeric, errors='coerce')
topics_subset['title_sentiment']=topics_subset['title_sentiment'].apply(pd.to_numeric, errors='coerce')
topics_subset['body_sentiment']=topics_subset['body_sentiment'].apply(pd.to_numeric, errors='coerce')
topics_subset['sentiment_skewed']=topics_subset['sentiment_skewed'].apply(pd.to_numeric, errors='coerce')
topics_subset['title_skewed']=topics_subset['title_skewed'].apply(pd.to_numeric, errors='coerce')
topics_subset['body_skewed']=topics_subset['body_skewed'].apply(pd.to_numeric, errors='coerce')

csv = pd.DataFrame(topics_subset)
export_csv = csv.to_csv (r'~/Downloads/prepped_data.csv', index = None, header=True)

print('yay! finished')

0
5000
10000
15000
20000
25000
30000
35000
40000
45000
got this far
even further now
yay! finished


In [4]:
topics_subset=topics_subset[topics_subset['comms_num'] >= 10]
topics_subset.dropna(subset = ["sentiment"], inplace=True)
topics_subset.dropna(subset = ["sentiment_skewed"], inplace=True)
topics_subset['title_vs_comments']=topics_subset['title_skewed']-topics_subset['sentiment_skewed']
topics_subset=topics_subset.sort_values('subreddit', ascending=False)
grouped_by=topics_subset.groupby('subreddit')['sentiment'].apply(list).reset_index(name='sentiments')
grouped_by_skew=topics_subset.groupby('subreddit')['sentiment_skewed'].apply(list).reset_index(name='sentiments')
grouped_by_title=topics_subset.groupby('subreddit')['title_skewed'].apply(list).reset_index(name='title')
# grouped_by=grouped_by.sort_values('subreddit', ascending=False)
# grouped_by_skew=grouped_by_skew.sort_values('subreddit', ascending=False)

In [5]:
grouped_by_skew['mean']=grouped_by_skew['subreddit']
grouped_by_skew['median']=grouped_by_skew['subreddit']
i=0
for i in range(len(grouped_by_skew['mean'])):
    grouped_by_skew['mean'][i]=mean(grouped_by_skew['sentiments'][i])
    i=+1
grouped_by_skew['mean']=grouped_by_skew['mean'].apply(pd.to_numeric, errors='coerce')

i=0
for i in range(len(grouped_by_skew['median'])):
    grouped_by_skew['median'][i]=median(grouped_by_skew['sentiments'][i])
    i=+1
grouped_by_skew['median']=grouped_by_skew['median'].apply(pd.to_numeric, errors='coerce')

max_positive_med=grouped_by_skew['median'].max()
min_positive_med=grouped_by_skew['median'].min()

most_positive_med=str(grouped_by_skew['subreddit'][grouped_by_skew.index[grouped_by_skew['median'] == max_positive_med].tolist()[0]])
least_positive_med=str(grouped_by_skew['subreddit'][grouped_by_skew.index[grouped_by_skew['median'] == min_positive_med].tolist()[0]])

max_positive_mean=grouped_by_skew['mean'].max()
min_positive_mean=grouped_by_skew['mean'].min()

most_positive_mean=str(grouped_by_skew['subreddit'][grouped_by_skew.index[grouped_by_skew['mean'] == max_positive_mean].tolist()[0]])
least_positive_mean=str(grouped_by_skew['subreddit'][grouped_by_skew.index[grouped_by_skew['mean'] == min_positive_mean].tolist()[0]])

In [6]:
# subreddits = ['Reddit','Reddit_Skewed']
# sentiments_1 = list(topics_subset['sentiment'])
# sentiments_2 = list(topics_subset['sentiment_skewed'])
# sentiments=[]
# sentiments.append(sentiments_1)
# sentiments.append(sentiments_2)
    
# colors = ['#333F44', '#37AA9C']
# fig = ff.create_distplot(sentiments, subreddits, show_hist=True, show_rug=False, bin_size=0.1)
# fig.show()

In [7]:
#subreddits = ['Comments','Comments_Skewed','Title','Title_Skewed','Body','Body_Skewed', ]
subreddits = ['Comments','Title', 'Difference: Title - Comments']
# subreddits = ['Comments_Skewed','Title_Skewed','Body_Skewed']

# sentiments_1 = list(topics_subset['sentiment'])
# sentiments_3 = list(topics_subset['title_sentiment'])
# sentiments_5 = list(topics_subset['body_sentiment'])


sentiments_2 = list(topics_subset['sentiment_skewed'])
sentiments_4 = list(topics_subset['title_skewed'])
sentiments_6 = list(topics_subset['title_vs_comments'])

sentiments=[]
# sentiments.append(sentiments_1)
# sentiments.append(sentiments_3)
# sentiments.append(sentiments_5)

sentiments.append(sentiments_2)
sentiments.append(sentiments_4)
sentiments.append(sentiments_6)
  
fig_1 = ff.create_distplot(sentiments, subreddits, show_hist=False, show_rug=False, bin_size=0.1)
fig_1.update_layout(template='plotly_dark',title={'text': "Reddit Comments Sentiment",'y':0.9,'x':0.5, 'xanchor': 'center','yanchor': 'top'}, xaxis_title={'text':"Comments sentiment <br> <i> -1 = Very Negative, 0 = Neutral, 1 = Very Positive</i>"}, yaxis_title="Observations")
fig_1.update_xaxes(range=[-1, 1])
fig_1.show()
figs.append('fig_1')

In [8]:
# subreddits = grouped_by['subreddit'].unique()
# sentiments = grouped_by['sentiments']
    
# colors = ['#333F44', '#37AA9C']
# fig = ff.create_distplot(sentiments, subreddits, show_hist=False, show_rug=False, bin_size=0.1)
# fig.show()

In [9]:
subreddits = list(grouped_by_skew['subreddit'].unique())
sentiments = list(grouped_by_skew['sentiments'])

subreddits.reverse()
sentiments.reverse()

subreddits.append('Reddit - all')
sentiments.append(list(topics_subset['sentiment_skewed']))

fig_2 = ff.create_distplot(sentiments, subreddits, show_hist=False, show_rug=False, bin_size=0.1)
fig_2.update_layout(template='plotly_dark',title={'text': "Reddit Comments Sentiment",'y':0.9,'x':0.5, 'xanchor': 'center','yanchor': 'top'}, xaxis_title={'text':"Comments sentiment <br> <i> -1 = Very Negative, 0 = Neutral, 1 = Very Positive</i>"}, yaxis_title="Observations")
fig_2.update_xaxes(range=[-1, 1])
fig_2.show()
figs.append('fig_2')

In [10]:
# subreddits = grouped_by_title['subreddit'].unique()
# sentiments = grouped_by_title['title']

# fig_3 = ff.create_distplot(sentiments, subreddits, show_hist=False, show_rug=False, bin_size=0.1)
# fig_3.update_layout(template='plotly_dark',title={'text': "Reddit Titles Sentiment",'y':0.9,'x':0.5, 'xanchor': 'center','yanchor': 'top'}, xaxis_title={'text':"Titles sentiment <br> <i> -1 = Very Negative, 0 = Neutral, 1 = Very Positive</i>"}, yaxis_title="Observations")
# fig_3.update_xaxes(range=[-1, 1])
# fig_3.show()
# figs.append('fig_3')

In [11]:
subreddits = ['All of Reddit',"Most Positive:<br>"+str(most_positive_med), "Most Negative:<br>"+str(least_positive_med)]
#subreddits = ['Reddit','1', '2']
sentiments = []

sentiments_1 = list(topics_subset['sentiment_skewed'])
sentiments_2 = grouped_by_skew['sentiments'][grouped_by_skew.index[grouped_by_skew['median'] == max_positive_med].tolist()[0]]
sentiments_3 = grouped_by_skew['sentiments'][grouped_by_skew.index[grouped_by_skew['median'] == min_positive_med].tolist()[0]]
# sentiments_2 = list((grouped_by_skew['sentiments'][grouped_by_skew.loc[grouped_by_skew['subreddit']==zsd].index]))
# sentiments_3 = list((grouped_by_skew['sentiments'][grouped_by_skew.loc[grouped_by_skew['subreddit']==sds].index]))
sentiments.append(sentiments_1)
sentiments.append(sentiments_2)
sentiments.append(sentiments_3)

fig_4 = ff.create_distplot(sentiments, subreddits, show_hist=False, show_rug=False, bin_size=0.1)
fig_4.update_layout(template='plotly_dark',title={'text': "Most and Least Positive Subreddits (Median)",'y':0.9,'x':0.5, 'xanchor': 'center','yanchor': 'top'}, xaxis_title={'text':"Titles sentiment <br> <i> -1 = Very Negative, 0 = Neutral, 1 = Very Positive</i>"}, yaxis_title="Observations")
fig_4.update_xaxes(range=[-1, 1])
fig_4.show()
figs.append('fig_4')

In [12]:
subreddits = ['All of Reddit',"Most Positive:<br>"+str(most_positive_mean), "Most Negative:<br>"+str(least_positive_mean)]
#subreddits = ['Reddit','1', '2']
sentiments = []
zsd='nottheonion'
sds='oddlysatisfying'

sentiments_1 = list(topics_subset['sentiment_skewed'])
sentiments_2 = grouped_by_skew['sentiments'][grouped_by_skew.index[grouped_by_skew['mean'] == max_positive_mean].tolist()[0]]
sentiments_3 = grouped_by_skew['sentiments'][grouped_by_skew.index[grouped_by_skew['mean'] == min_positive_mean].tolist()[0]]
# sentiments_2 = list((grouped_by_skew['sentiments'][grouped_by_skew.loc[grouped_by_skew['subreddit']==zsd].index]))
# sentiments_3 = list((grouped_by_skew['sentiments'][grouped_by_skew.loc[grouped_by_skew['subreddit']==sds].index]))
sentiments.append(sentiments_1)
sentiments.append(sentiments_2)
sentiments.append(sentiments_3)

fig_5 = ff.create_distplot(sentiments, subreddits, show_hist=False, show_rug=False, bin_size=0.1)
fig_5.update_layout(template='plotly_dark',title={'text': "Most and Least Positive Subreddits (Mean)",'y':0.9,'x':0.5, 'xanchor': 'center','yanchor': 'top'}, xaxis_title={'text':"Titles sentiment <br> <i> -1 = Very Negative, 0 = Neutral, 1 = Very Positive</i>"}, yaxis_title="Observations")
fig_5.update_xaxes(range=[-1, 1])
fig_5.show()
figs.append('fig_5')

In [13]:
min_positive_post=topics_subset['sentiment_skewed'].min()
min_positive_post_id=str(topics_subset['id'][topics_subset.index[topics_subset['sentiment_skewed'] == min_positive_post].tolist()[0]])

max_positive_post=topics_subset['sentiment_skewed'].max()
max_positive_post_id=str(topics_subset['id'][topics_subset.index[topics_subset['sentiment_skewed'] == max_positive_post].tolist()[0]])

In [14]:
print("reddit.com/"+min_positive_post_id)
print("reddit.com/"+max_positive_post_id)

reddit.com/ctgoky
reddit.com/f2li13


In [15]:
topics_more = pd.read_csv (r'~/Downloads/topics_more.csv')

topics_more['comments']=topics_more['comments'].astype(str)
topics_more['title']=topics_more['title'].astype(str)
topics_more['body']=topics_more['body'].astype(str)

REPLACE_NO_SPACE = re.compile("[.;:!\'?,\"()\[\]]")
REPLACE_WITH_SPACE = re.compile("(<br\s*/><br\s*/>)|(\-)|(\/)")


#phrases=df_all['Phrase'].tolist()
topics_more['comments_clean']=topics_more['comments']
topics_more['title_clean']=topics_more['comments']
topics_more['body_clean']=topics_more['comments']
# random.shuffle(phrases)
# train_split=.75
# train_len=int(len(phrases)*train_split)
# print(train_len)

# phrases_train = phrases[:train_len]
# phrases_test = phrases[train_len:]

def preprocess_phrase(phrases):
    phrases = [REPLACE_NO_SPACE.sub("", line.lower()) for line in phrases]
    phrases = [REPLACE_WITH_SPACE.sub(" ", line) for line in phrases]
    
    return phrases

topics_more['comments_clean'] = preprocess_phrase(topics_more['comments'])
topics_more['title_clean'] = preprocess_phrase(topics_more['title'])
topics_more['body_clean'] = preprocess_phrase(topics_more['body'])
topics_more=topics_more.reset_index(drop=True)

topics_more['blob']=topics_more['comments']
topics_more['sentiment']=topics_more['comments_clean']
topics_more['title_sentiment']=topics_more['comments_clean']
topics_more['body_sentiment']=topics_more['comments_clean']
i=0
for i in range(len(topics_more['comments_clean'])):
    if i%5000==0:
        print(i)
    topics_more['blob'][i]=TextBlob(topics_more['comments_clean'][i])
    topics_more['sentiment'][i]=topics_more['blob'][i].sentiment.polarity
    topics_more['title_sentiment'][i]=TextBlob(topics_more['title_clean'][i]).sentiment.polarity
    topics_more['body_sentiment'][i]=TextBlob(topics_more['body_clean'][i]).sentiment.polarity
    
    i=+1

topics_more['sentiment_skewed']=topics_more['sentiment']
i=0
for i in range(len(topics_more['sentiment'])):
    if topics_more['sentiment'][i]>0:
        topics_more['sentiment_skewed'][i]=topics_more['sentiment'][i]*(1+((1-topics_more['sentiment'][i])**2))
    elif topics_more['sentiment'][i]<0:
        topics_more['sentiment_skewed'][i]=topics_more['sentiment'][i]*(1+((-1-topics_more['sentiment'][i])**2))
    else:
        topics_more['sentiment_skewed'][i]=0
    i=+1
print('got this far')
    
topics_more['title_skewed']=topics_more['sentiment']
i=0
for i in range(len(topics_more['sentiment'])):
    if topics_more['title_sentiment'][i]>0:
        topics_more['title_skewed'][i]=topics_more['title_sentiment'][i]*(1+((1-topics_more['title_sentiment'][i])**2))
    elif topics_more['title_sentiment'][i]<0:
        topics_more['title_skewed'][i]=topics_more['title_sentiment'][i]*(1+((-1-topics_more['title_sentiment'][i])**2))
    else:
        topics_more['title_skewed'][i]=0
    i=+1
print('even further now')
    
topics_more['body_skewed']=topics_more['sentiment']
i=0
for i in range(len(topics_more['sentiment'])):
    if topics_more['body_sentiment'][i]>0:
        topics_more['body_skewed'][i]=topics_more['body_sentiment'][i]*(1+((1-topics_more['body_sentiment'][i])**2))
    elif topics_more['body_sentiment'][i]<0:
        topics_more['body_skewed'][i]=topics_more['body_sentiment'][i]*(1+((-1-topics_more['body_sentiment'][i])**2))
    else:
        topics_more['body_skewed'][i]=0
    i=+1

topics_more['sentiment']=topics_more['sentiment'].apply(pd.to_numeric, errors='coerce')
topics_more['title_sentiment']=topics_more['title_sentiment'].apply(pd.to_numeric, errors='coerce')
topics_more['body_sentiment']=topics_more['body_sentiment'].apply(pd.to_numeric, errors='coerce')
topics_more['sentiment_skewed']=topics_more['sentiment_skewed'].apply(pd.to_numeric, errors='coerce')
topics_more['title_skewed']=topics_more['title_skewed'].apply(pd.to_numeric, errors='coerce')
topics_more['body_skewed']=topics_more['body_skewed'].apply(pd.to_numeric, errors='coerce')

csv = pd.DataFrame(topics_more)
export_csv = csv.to_csv (r'~/Downloads/prepped_data_more.csv', index = None, header=True)

print('yay! finished')

topics_more=topics_more[topics_more['comms_num'] >= 10]
topics_more.dropna(subset = ["sentiment"], inplace=True)
topics_more.dropna(subset = ["sentiment_skewed"], inplace=True)
topics_more['title_vs_comments']=topics_more['title_skewed']-topics_more['sentiment_skewed']
topics_more=topics_more.sort_values('subreddit', ascending=True)
grouped_by_more=topics_more.groupby('subreddit')['sentiment'].apply(list).reset_index(name='sentiments')
grouped_by_skew_more=topics_more.groupby('subreddit')['sentiment_skewed'].apply(list).reset_index(name='sentiments')
grouped_by_title_more=topics_more.groupby('subreddit')['title_skewed'].apply(list).reset_index(name='title')

0
got this far
even further now
yay! finished


In [16]:
more_reddits = list(grouped_by_skew_more['subreddit'].unique())
# sentiments = list(grouped_by_skew['sentiments'])
for reddit in more_reddits:
    subreddits = ['All of Reddit', str(reddit)]
    #subreddits = ['Reddit','1', '2']
    sentiments = []
    sentiments_1 = list(topics_subset['sentiment_skewed'])
    sentiments_2 = grouped_by_skew_more['sentiments'][grouped_by_skew_more.index[grouped_by_skew_more['subreddit'] == reddit].tolist()[0]]
    sentiments.append(sentiments_1)
    sentiments.append(sentiments_2)
    name='fig_'+str(reddit)
    globals()[name] = ff.create_distplot(sentiments, subreddits, show_hist=False, show_rug=False, bin_size=0.1)
    eval(name).update_layout(template='plotly_dark',title={'text': str(reddit)+" vs the rest of Reddit",'y':0.9,'x':0.5, 'xanchor': 'center','yanchor': 'top'}, xaxis_title={'text':"Titles sentiment <br> <i> -1 = Very Negative, 0 = Neutral, 1 = Very Positive</i>"}, yaxis_title="Observations")
    eval(name).update_xaxes(range=[-1, 1])
#     eval(name).show()
    figs.append(str(name))

In [17]:
username = 'sweeney_khs' # your username
api_key = 'gyxuqJ5FScmgneLxIEFU' # your api key - go to profile > settings > regenerate key
chart_studio.tools.set_credentials_file(username=username, api_key=api_key)

In [18]:
pio.write_html(fig_2, file='index.html', auto_open=True)

In [19]:
if not os.path.exists("images"):
    os.mkdir("images")

figs=list(set(figs))
for fig in figs:
    eval(fig).write_image("images/"+str(fig)+".png")

In [20]:
print(figs)

['fig_4', 'fig_rugbyunion', 'fig_1', 'fig_2', 'fig_5', 'fig_hellointernet']


In [21]:
# py.plot(fig, filename = 'reddit_sentiment', auto_open=True)

In [22]:
# tls.get_embed('https://sweeneykhs.github.io/reddit_sentiment/') #change to your url

In [23]:
<iframe id="igraph" scrolling="no" style="border:none;" seamless="seamless" src="https://sweeneykhs.github.io/reddit_sentiment/" height="525" width="100%"></iframe>

SyntaxError: invalid syntax (<ipython-input-23-80c8ee298da1>, line 1)